In [6]:
import nltk

# Generate Alternatives 

Create BK-Tree

In [7]:
class BKTree:
    def __init__(self, distfn, words):
        """
        Create a new BK-tree from the given distance function and
        words.
        
        Arguments:
        distfn: a binary function that returns the distance between
        two words.  Return value is a non-negative integer.  the
        distance function must be a metric space.
        
        words: an iterable.  produces values that can be passed to
        distfn
        
        """
        self.distfn = distfn

        it = iter(words)
        root = next(it)
        self.tree = (root, {})

        for i in it:
            self._add_word(self.tree, i)

    def _add_word(self, parent, word):
        pword, children = parent
        d = self.distfn(word, pword)
        if d in children:
            self._add_word(children[d], word)
        else:
            children[d] = (word, {})

    def query(self, word, n):
        """
        Return all words in the tree that are within a distance of `n'
        from `word`.  
        Arguments:
        
        word: a word to query on
        n: a non-negative integer that specifies the allowed distance
        from the query word.  
        
        Return value is a list of tuples (distance, word), sorted in
        ascending order of distance.
        
        """
        def rec(parent):
            pword, children = parent
            d = self.distfn(word, pword)
            results = []
            if d <= n:
                results.append( (d, pword) )
                
            for i in range(d-n, d+n+1):
                child = children.get(i)
                if child is not None:
                    results.extend(rec(child))
            return results

        # sort by distance
        return sorted(rec(self.tree))
    


def brute_query(word, words, distfn, n):
    """A brute force distance query
    Arguments:
    word: the word to query for
    words: a iterable that produces words to test
    distfn: a binary function that returns the distance between a
    `word' and an item in `words'.
    n: an integer that specifies the distance of a matching word
    
    """
    return [i for i in words
            if distfn(i, word) <= n]


def maxdepth(tree, count=0):
    _, children = t
    if len(children):
        return max(maxdepth(i, c+1) for i in children.values())
    else:
        return c


# http://en.wikibooks.org/wiki/Algorithm_implementation/Strings/Levenshtein_distance#Python
def levenshtein(s, t):
    m, n = len(s), len(t)
    d = [range(n+1)]
    d += [[i] for i in range(1,m+1)]
    for i in range(0,m):
        for j in range(0,n):
            cost = 1
            if s[i] == t[j]: cost = 0

            d[i+1].append( min(d[i][j+1]+1, # deletion
                               d[i+1][j]+1, #insertion
                               d[i][j]+cost) #substitution
                           )
    return d[m][n]


def dict_words(dictfile="/usr/share/dict/american-english"):
    "Return an iterator that produces words in the given dictionary."
    return filter(len,
                   map(str.strip,
                        open(dictfile)))


def timeof(fn, *args):
    import time
    t = time.time()
    res = fn(*args)
    print ("time: ", (time.time() - t))
    return res



if __name__ == "__main__":

    tree = BKTree(levenshtein,
                  dict_words('dictionary.txt'))



In [8]:
print (tree.query("fries", 2))

[(1, 'Aries'), (2, 'Ares'), (2, 'Brie'), (2, 'Erie'), (2, 'Uris'), (2, 'brief'), (2, 'crises'), (2, 'criss'), (2, 'feces'), (2, 'fief'), (2, 'free'), (2, 'fresh'), (2, 'fret'), (2, 'friar'), (2, 'friend'), (2, 'frieze'), (2, 'frill'), (2, 'grief'), (2, 'iris'), (2, 'priest'), (2, 'series')]


In [9]:
len(tree.query("fries", 2))

21

# Get Alternatives

In [10]:
def get_alternatives(word,tree,max_distance):
    edit_distances=[]
    alternatives=[]
    dict_alter=tree.query(word, max_distance)
    for a in range(len(dict_alter)):
        alternatives.append(dict_alter[a][1])
        edit_distances.append(dict_alter[a][0])
    return alternatives, edit_distances
        
alter, edit_distances = get_alternatives("troupe",tree,2)
print(alter)
print(edit_distances)
    

['troupe', 'trompe', 'arouse', 'coupe', 'drupe', 'grope', 'group', 'grouse', 'rope', 'rouge', 'rouse', 'route', 'tripe', 'triune', 'troop', 'trouble', 'trough', 'trounce', 'trouser', 'trout', 'truce', 'true']
[0, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]


# Language Model


In [11]:
nltk.download('reuters')

from nltk.corpus import reuters
from nltk import bigrams, trigrams
from collections import Counter, defaultdict


model = defaultdict(lambda: defaultdict(lambda: 0))
#LM counts 
for sentence in reuters.sents():
    for w1, w2 in bigrams(sentence, pad_right=True, pad_left=True):
        model[w1][w2] += 1
        
# counts to probabilities
for w1 in model:
    total_count = float(sum(model[w1].values()))
    for w2 in model[w1]:
        model[w1][w2] /= total_count


[nltk_data] Downloading package reuters to
[nltk_data]     /Users/vuthanhtrung/nltk_data...
[nltk_data]   Unzipping corpora/reuters.zip.


In [8]:
model

defaultdict(<function __main__.<lambda>()>,
            {None: defaultdict(<function __main__.<lambda>.<locals>.<lambda>()>,
                         {'ASIAN': 7.31047591198187e-05,
                          'They': 0.008151180641859785,
                          'But': 0.019263104028072228,
                          'The': 0.16154324146501936,
                          'Unofficial': 1.8276189779954676e-05,
                          '"': 0.06559324512025733,
                          'In': 0.02522114189633745,
                          'Threat': 3.655237955990935e-05,
                          'Taiwan': 0.0006944952116382777,
                          'Retaliation': 5.482856933986402e-05,
                          'A': 0.013963008991885371,
                          'Last': 0.0036917903355508444,
                          'Much': 0.0001462095182396374,
                          'He': 0.028986036991008116,
                          'Meanwhile': 0.0007493237809781417,
                   

# Get Language Model probability

In [12]:
def Probability_LM(prev_word,word,model):
    return model[prev_word][word]

# Word Frequency

In [14]:
import nltk
#nltk.download('brown')
#nltk.download('universal_tagset')
data = nltk.corpus.brown.tagged_sents(tagset='universal')
dict_voc = dict()
set_voc = list()
set_tag = list()
for phr in data:
  for mot in phr:
    if not(mot[0] in set_voc):
      set_voc.append(mot[0])
      dict_voc[mot[0]]=0
    dict_voc[mot[0]]+=1
    if not(mot[1] in set_tag):
      set_tag.append(mot[1])

[nltk_data] Downloading package brown to
[nltk_data]     /Users/vuthanhtrung/nltk_data...
[nltk_data]   Package brown is already up-to-date!
[nltk_data] Downloading package universal_tagset to
[nltk_data]     /Users/vuthanhtrung/nltk_data...
[nltk_data]   Package universal_tagset is already up-to-date!


# Get word frequency

In [15]:
def get_word_frequency(dict_voc,word):
    return dict_voc[word]

# Construct Alternatives Table

In [16]:
def construct_table(sentence_to_correct,word_to_correct,model,tree,max_distance):
    #get alternatives adn edit distances
    alternatives,edit_distances=get_alternatives(word_to_correct,tree,max_distance)
    #tokenize sentence to correct
    tokens = nltk.word_tokenize(sentence_to_correct)
    word_to_correct_index=tokens.index(word_to_correct)
    #Get previous word
    previous_word=tokens[word_to_correct_index-1]
    P_LM=[]
    for word in alternatives:
        P_LM.append(Probability_LM(previous_word,word_to_correct,model))
    #get words frequencies
    frequencies=[]
    for word in alternatives:
        if word in dict_voc:
            frequencies.append(get_word_frequency(dict_voc,word))
        else:
            frequencies.append(0)
    #get words lengths
    lengths_G=[]
    lengths_L=[]
    lengths_E=[]
    N=len(word_to_correct)
    for word in alternatives:
        if (len(word)>N):
            lengths_G.append(1)
            lengths_L.append(0)
            lengths_E.append(0)

        elif(len(word)==N):
            lengths_G.append(0)
            lengths_L.append(0)
            lengths_E.append(1)
        else:
            lengths_G.append(0)
            lengths_L.append(1)
            lengths_E.append(0)
        
    return alternatives,edit_distances,P_LM,frequencies,lengths_G,lengths_E,lengths_L
construct_table("I am eating french fries .","fries",model,tree,2)


(['Aries',
  'Ares',
  'Brie',
  'Erie',
  'Uris',
  'brief',
  'crises',
  'criss',
  'feces',
  'fief',
  'free',
  'fresh',
  'fret',
  'friar',
  'friend',
  'frieze',
  'frill',
  'grief',
  'iris',
  'priest',
  'series'],
 [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2],
 [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
 [0, 1, 0, 2, 0, 70, 21, 0, 0, 0, 243, 76, 1, 0, 125, 13, 0, 10, 0, 16, 122],
 [0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1],
 [1, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0, 0],
 [0, 1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0])

In [17]:
#Train_set
import csv
filename='train.csv'
Sentence=[]
Error=[]
Correction=[]
with open(filename, mode='r') as csv_file:
    csv_reader = csv.DictReader(csv_file)
    line_count = 0
    for row in csv_reader:
        if line_count == 0:
            line_count += 1
        Sentence.append(f'{row["Sentence"]}')
        Error.append(f'{row["error"]}')
        Correction.append(f'{row["correction"]}')
        line_count += 1


In [18]:
Sentence[]

'By the 1780s the goals of England were so full that convicts were often chained up in rotting old ships.'

In [42]:
Error[0]
            

'goals'

In [43]:
Correction[0]

'jails'

In [51]:
p = construct_table(Sentence[1],"goals",model,tree,3)

ValueError: 'jails' is not in list

In [24]:
# Load scikit's random forest classifier library
from sklearn.ensemble import RandomForestClassifier
from sklearn import linear_model
# Load pandas
import pandas as pd

# Load numpy
import numpy as np

# Set random seed
np.random.seed(0)

In [25]:
# Create a random forest Classifier. By convention, clf means 'Classifier'
clf = linear_model.SGDClassifier(max_iter=1000)
classes = np.zeros(2)
classes[1]=1
for i, phrase in enumerate(Sentence):
    print(i)
    alternatives,edit_distances,P_LM,frequencies,lengths_G,lengths_E,lengths_L = \
                construct_table(phrase,Error[i],model,tree,3)
    train_set=np.column_stack((edit_distances,P_LM,frequencies,lengths_G,lengths_E,lengths_L))
    #print(train_set.shape)
    label_set=np.zeros(train_set.shape[0])
    if Correction[i] in alternatives:
        label_set[alternatives.index(Correction[i])]=1
    clf.partial_fit(train_set, label_set, classes=classes)

0
1
2
3
4
5
6


In [26]:
len(construct_table("i am not very fatr","fatr",model,tree,3)[0])

1266

In [27]:
def build_test_set(sentence,wrong_word,model,tree,max_distance):
    alternatives,edit_distances,P_LM,frequencies,lengths_G,lengths_E,lengths_L = \
                    construct_table(sentence,wrong_word,model,tree,max_distance)
    test_set=np.column_stack((edit_distances,P_LM,frequencies,lengths_G,lengths_E,lengths_L))
    return test_set
test_set = build_test_set("i am not very fatr","fatr",model,tree,3)

In [28]:
e = clf.predict(test_set)
np.max(e)

0.0